# FOR COLLECTING HAND IMAGES FROM WEBCAM

In [1]:
import cv2
from cvzone.HandTrackingModule import HandDetector
import numpy as np
import math
import time
import os
import csv
import copy
import itertools

# Initialize webcam
cap = cv2.VideoCapture(0)

# Initialize hand detector
detector = HandDetector(maxHands=1)

# Constants
offset = 20
imgSize = 500
baseFolder = "C:/Users/User/OneDrive/Documents/SignLanguageApp/SLangDataset/testData"
letters = ["A", "B", "C", "D", "D2", "E", "F", "F2", "G", "H", "I", "J",
           "K", "L", "M", "N", "O", "P", "Q", "R", "S", "T",
           "U", "V", "W", "X", "Y", "Z", "space"]
captureInterval = 0.001  # Interval between captures in seconds

# Pre-process landmarks
def pre_process_landmark(landmark_list):
    temp_landmark_list = copy.deepcopy(landmark_list)

    # Convert to relative coordinates
    base_x, base_y, base_z = 0, 0, 0
    for index, landmark_point in enumerate(temp_landmark_list):
        if index == 0:
            base_x, base_y , base_z = landmark_point[0], landmark_point[1], landmark_point[2]

        temp_landmark_list[index][0] -= base_x
        temp_landmark_list[index][1] -= base_y
        temp_landmark_list[index][2] -= base_z

    # Convert to a one-dimensional list
    temp_landmark_list = list(
        itertools.chain.from_iterable(temp_landmark_list))

    # Normalization
    max_value = max(list(map(abs, temp_landmark_list))) if temp_landmark_list else 1

    def normalize_(n):
        return n / max_value

    temp_landmark_list = list(map(normalize_, temp_landmark_list))

    return temp_landmark_list

# Global CSV file for all classes
global_csv_file_path = os.path.join(baseFolder, "all_classes_landmarks.csv")

# Ensure the base folder exists
os.makedirs(baseFolder, exist_ok=True)

# Create global CSV file and write header
with open(global_csv_file_path, mode='w', newline='') as global_csv_file:
    global_csv_writer = csv.writer(global_csv_file)
    header = ['ClassName', 'ImageName'] + [f'Point{i}_{coord}' for i in range(21) for coord in ('x', 'y', 'z')]
    global_csv_writer.writerow(header)

    # Loop through each letter
    for className in letters:
        print(f"Starting collection for class: {className}")
        folder = os.path.join(baseFolder, className)
        os.makedirs(folder, exist_ok=True)

        # Initialize counter for the current class
        counter = 0
        maxImages = 300

        collecting = False

        while counter < maxImages:
            success, img = cap.read()
            if not success:
                print("Failed to access camera.")
                break

            # Detect hands in the image
            hands, img = detector.findHands(img)
            if hands:
                hand = hands[0]
                x, y, w, h = hand['bbox']
                lm_list = hand['lmList']  # Hand landmark list

                # Create a white canvas
                imgWhite = np.ones((imgSize, imgSize, 3), np.uint8) * 255

                # Crop the image around the detected hand
                imgCrop = img[y - offset:y + h + offset, x - offset:x + w + offset]

                # Prevent errors from invalid crop boundaries
                if imgCrop.size == 0:
                    continue

                aspectRatio = h / w

                try:
                    if aspectRatio > 1:
                        # Height is greater than width
                        k = imgSize / h
                        wCal = math.ceil(k * w)
                        imgResize = cv2.resize(imgCrop, (wCal, imgSize))
                        wGap = math.ceil((imgSize - wCal) / 2)
                        imgWhite[:, wGap:wCal + wGap] = imgResize
                    else:
                        # Width is greater than height
                        k = imgSize / w
                        hCal = math.ceil(k * h)
                        imgResize = cv2.resize(imgCrop, (imgSize, hCal))
                        hGap = math.ceil((imgSize - hCal) / 2)
                        imgWhite[hGap:hCal + hGap, :] = imgResize

                    # Convert to grayscale
                    imgGray = cv2.cvtColor(imgWhite, cv2.COLOR_BGR2GRAY)

                    # Display the processed images
                    cv2.imshow("ImageCrop", imgCrop)
                    cv2.imshow("ImageWhite (Grayscale)", imgGray)
                except Exception as e:
                    print(f"Error processing image: {e}")
                    continue

                if collecting:
                    # Save the image and landmarks
                    counter += 1
                    fileName = f"{className.lower()}_{counter}.jpg"
                    filePath = os.path.join(folder, fileName)
                    cv2.imwrite(filePath, imgGray)  # Save grayscale image

                    # Normalize and save landmarks
                    normalized_lm_list = pre_process_landmark(lm_list)
                    global_csv_writer.writerow([className, fileName] + normalized_lm_list)
                    print(f"Saved {counter}/{maxImages} images and landmarks for class {className}")

            # Display the original image
            cv2.imshow("Image", img)

            # Check for key press
            key = cv2.waitKey(1)
            if key == ord('q'):
                collecting = True

            # Wait for the interval
            time.sleep(captureInterval)

        print(f"Completed collection for {className}.")
        input("Press 'Enter' to continue to the next letter.")

# Release the webcam and close windows
cap.release()
cv2.destroyAllWindows()

Starting collection for class: A
Saved 1/300 images and landmarks for class A
Saved 2/300 images and landmarks for class A
Saved 3/300 images and landmarks for class A
Saved 4/300 images and landmarks for class A
Saved 5/300 images and landmarks for class A
Saved 6/300 images and landmarks for class A
Saved 7/300 images and landmarks for class A
Saved 8/300 images and landmarks for class A
Saved 9/300 images and landmarks for class A
Saved 10/300 images and landmarks for class A
Saved 11/300 images and landmarks for class A
Saved 12/300 images and landmarks for class A
Saved 13/300 images and landmarks for class A
Saved 14/300 images and landmarks for class A
Saved 15/300 images and landmarks for class A
Saved 16/300 images and landmarks for class A
Saved 17/300 images and landmarks for class A
Saved 18/300 images and landmarks for class A
Saved 19/300 images and landmarks for class A
Saved 20/300 images and landmarks for class A
Saved 21/300 images and landmarks for class A
Saved 22/3

### DATA SAVED IN SLangDataset/newData [sub folders for image classes, 1 csv file for coordinates]

# FOR EXISTING IMAGE DATASET

In [7]:
import cv2
from cvzone.HandTrackingModule import HandDetector
import os
import csv
import itertools
import copy

# Initialize hand detector
detector = HandDetector(maxHands=1)

# Constants
fixedSize = 300  # Fixed dimensions for cropped images
baseFolder = "C:/Users/User/OneDrive/Documents/SignLanguageApp/SLangDataset/asl-alphabet/asl_alphabet_train/asl_alphabet_train"
outputFolder = "C:/Users/User/OneDrive/Documents/SignLanguageApp/SLangDataset/croppedBWData2"
outputCsv = os.path.join(outputFolder, "cropped_bw_landmarks2.csv")

# Pre-process landmarks
def pre_process_landmark(landmark_list):
    temp_landmark_list = copy.deepcopy(landmark_list)

    # Convert to relative coordinates
    base_x, base_y, base_z = 0, 0, 0
    for index, landmark_point in enumerate(temp_landmark_list):
        if index == 0:
            base_x, base_y, base_z = landmark_point[0], landmark_point[1], landmark_point[2]

        temp_landmark_list[index][0] -= base_x
        temp_landmark_list[index][1] -= base_y
        temp_landmark_list[index][2] -= base_z

    # Convert to a one-dimensional list
    temp_landmark_list = list(itertools.chain.from_iterable(temp_landmark_list))

    # Normalization
    max_value = max(list(map(abs, temp_landmark_list))) if temp_landmark_list else 1

    def normalize_(n):
        return n / max_value

    temp_landmark_list = list(map(normalize_, temp_landmark_list))

    return temp_landmark_list

# Ensure output folder exists
os.makedirs(outputFolder, exist_ok=True)

# Create CSV file and write header
with open(outputCsv, mode='w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    header = ['ClassName', 'ImageName'] + [f'Point{i}_{coord}' for i in range(21) for coord in ('x', 'y', 'z')]
    csv_writer.writerow(header)

    # Iterate over each class folder
    for className in os.listdir(baseFolder):
        classPath = os.path.join(baseFolder, className)
        if not os.path.isdir(classPath):
            continue  # Skip non-directory files

        print(f"Processing class: {className}")
        croppedClassFolder = os.path.join(outputFolder, className)
        os.makedirs(croppedClassFolder, exist_ok=True)

        # Iterate over each image in the class folder
        for imgName in os.listdir(classPath):
            imgPath = os.path.join(classPath, imgName)
            if not imgName.lower().endswith(('.png', '.jpg', '.jpeg')):
                continue  # Skip non-image files

            # Read the image
            img = cv2.imread(imgPath)

            # Detect hands in the image
            hands, img = detector.findHands(img, draw=True)  # Draw landmarks and lines on the image
            if hands:
                hand = hands[0]
                x, y, w, h = hand['bbox']  # Bounding box coordinates
                lm_list = hand['lmList']  # Hand landmark list

                # Crop the image around the bounding box
                imgCrop = img[y:y + h, x:x + w]

                # Prevent errors from invalid crop boundaries
                if imgCrop.size == 0:
                    continue

                # Resize the cropped image to the fixed size
                imgCropResized = cv2.resize(imgCrop, (fixedSize, fixedSize))

                # Convert to black and white (grayscale)
                imgCropBW = cv2.cvtColor(imgCropResized, cv2.COLOR_BGR2GRAY)

                # Save the cropped black-and-white image
                croppedImgPath = os.path.join(croppedClassFolder, imgName)
                cv2.imwrite(croppedImgPath, imgCropBW)

                # Normalize and save landmarks
                normalized_lm_list = pre_process_landmark(lm_list)
                csv_writer.writerow([className, imgName] + normalized_lm_list)
                print(f"Cropped, converted to black-and-white, and saved: {imgName}")

print("\nProcessing complete. Data saved to:")
print(f"Cropped Black-and-White Images: {outputFolder}")
print(f"CSV: {outputCsv}")


Processing class: A
Cropped, converted to black-and-white, and saved: A1.jpg
Cropped, converted to black-and-white, and saved: A10.jpg
Cropped, converted to black-and-white, and saved: A100.jpg
Cropped, converted to black-and-white, and saved: A1000.jpg
Cropped, converted to black-and-white, and saved: A1001.jpg
Cropped, converted to black-and-white, and saved: A1002.jpg
Cropped, converted to black-and-white, and saved: A1003.jpg
Cropped, converted to black-and-white, and saved: A1004.jpg
Cropped, converted to black-and-white, and saved: A1005.jpg
Cropped, converted to black-and-white, and saved: A1006.jpg
Cropped, converted to black-and-white, and saved: A1007.jpg
Cropped, converted to black-and-white, and saved: A1008.jpg
Cropped, converted to black-and-white, and saved: A1009.jpg
Cropped, converted to black-and-white, and saved: A101.jpg
Cropped, converted to black-and-white, and saved: A1010.jpg
Cropped, converted to black-and-white, and saved: A1011.jpg
Cropped, converted to black